In [1]:
from glob import glob
import json
path = "/future/u/gharshit/lotus-research/baselines/deepresearcher/outputs/lotus-research/deepresearcher-evaluate3/rollout/rollout_*_step_0.json"
files = glob(path)

with open("/future/u/gharshit/lotus-research/baselines/deepresearcher/outputs/lotus-research/deepresearcher-evaluate3/val_metrics.json", "r") as f:
    latencies = [ x["gen"] for x in json.load(f)["val/time"] ]

results = [None] * len(files)
print(results)
for file in files:
    result = {}
    with open(file, 'r') as f:
        data = json.load(f)
    i = int(file.split('rollout_')[-1].split('_')[0])
    result['latency'] = latencies[i]
    result['question'] = data[0]['question']
    result['messages'] = data[0]['messages']
    result['abstract'] = '\n'.join(result['question'].split('\n')[1:])
    tool_calls = []
    for x in data[0]['messages']:
        if 'tool_call' in x:
            tool_calls.append(x['tool_call'])
    result['tool_calls'] = tool_calls
    result['tool_response'] = []
    result['ctxs'] = []
    for x in data[0]['messages']:
        if x['role'] == 'tool':
            ctxs = json.loads(x['content'])
            result['tool_response'].append(ctxs)
            result['ctxs'] += [
                {
                    'search_query': ctx['search_query'],
                    "title": webpage['title'],
                    'text': webpage['quick_summary'],
                    'url': webpage['url'],
                    'id': webpage['url']
                }
                for ctx in ctxs
                for webpage in ctx['web_page_info_list']
            ]
    result['output'] = data[0]['messages'][-1]['content']
    results[i] = result

[None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None]


In [2]:
latencies

[41.831924070138484,
 52.44798175408505,
 44.80617945594713,
 53.97731858398765,
 86.78396304696798,
 37.79029712895863,
 12.49146371614188,
 41.155457423999906,
 47.01296263188124,
 32.964011253090575,
 74.61626312579028,
 38.04605526407249,
 41.64913183497265,
 45.91657093097456,
 30.45811947900802,
 43.83124318206683,
 29.726980342995375,
 80.17647199612111,
 69.3815110239666,
 31.869078652001917,
 32.37375690508634,
 79.00299738510512,
 65.09840456885286,
 11.807887990027666,
 76.63152088597417,
 28.1449776829686]

In [3]:
results[0]

{'latency': 41.831924070138484,
 'question': 'Write a Related Works section for my academic paper. Here is my paper abstract:\nWe introduce AegisLLM, a cooperative multi-agent defense against adversarial attacks and information leakage. In AegisLLM, a structured workflow of autonomous agents — orchestrator, deflector, responder, and evaluator — collaborate to ensure safe and compliant LLM outputs, while self-improving over time through prompt optimization. We show that scaling agentic reasoning system at test-time—both by incorporating additional agent roles and by leveraging automated prompt optimization (such as DSPy)— substantially enhances robustness without compromising model utility. This test-time defense enables real-time adaptability to evolving attacks, without requiring model retraining. Comprehensive evaluations across key threat scenarios, including unlearning and jailbreaking, demonstrate the effectiveness of AegisLLM. On the WMDP unlearning benchmark, AegisLLM achieves n

In [1]:
import json

with open('/future/u/gharshit/lotus-research/baselines/deepresearcher/outputs/lotus-research/deepresearcher-evaluate/rollout/rollout_step_0.json', 'r') as f:
    data = json.load(f)

In [2]:
data

[{'idx': 0,
  'question': 'Write a Related Works section for my academic paper. Here is my paper abstract:\nWe introduce AegisLLM, a cooperative multi-agent defense against adversarial attacks and information leakage. In AegisLLM, a structured workflow of autonomous agents — orchestrator, deflector, responder, and evaluator — collaborate to ensure safe and compliant LLM outputs, while self-improving over time through prompt optimization. We show that scaling agentic reasoning system at test-time—both by incorporating additional agent roles and by leveraging automated prompt optimization (such as DSPy)— substantially enhances robustness without compromising model utility. This test-time defense enables real-time adaptability to evolving attacks, without requiring model retraining. Comprehensive evaluations across key threat scenarios, including unlearning and jailbreaking, demonstrate the effectiveness of AegisLLM. On the WMDP unlearning benchmark, AegisLLM achieves near-perfect unlearn

In [3]:
data[0]['message_str']

'<|im_start|>system\n## Background information \n* Today is 2025-05-21\n* You are Deep AI Research Assistant\n\nThe question I give you is a complex question that requires a *deep research* to answer.\n\nI will provide you with two tools to help you answer the question:\n* A web search tool to help you perform google search. \n* A webpage browsing tool to help you get new page content.\n\nYou don\'t have to answer the question now, but you should first think about the research plan or what to search next.\n\nYour output format should be one of the following two formats:\n\n<think>\nYOUR THINKING PROCESS\n</think>\n<answer>\nYOUR ANSWER AFTER GETTING ENOUGH INFORMATION\n</answer>\n\nor\n\n<think>\nYOUR THINKING PROCESS\n</think>\n<tool_call>\nYOUR TOOL CALL WITH CORRECT FORMAT\n</tool_call>\n\nYou should always follow the above two formats strictly.\nOnly output the final answer (in words, numbers or phrase) inside the <answer></answer> tag, without any explanations or extra information

In [4]:
x = data[10]['message_str'].split('<|im_start|>')[1:]

In [16]:
import ast

results = data.copy()
for i, result in enumerate(results):
    x = result['message_str'].split('<|im_start|>')[1:]
    result['abstract'] = '\n'.join(result['question'].split('\n')[1:])
    print(i, x)
    result['tool_calls'] = []
    result['tool_response'] = []
    result['ctxs'] = []
    for i in range(2, len(x)):
        if 'tool_call' in x[i]:
            result['tool_calls'].append(x[i].split('<tool_call>')[-1].split('</tool_call>')[0])
            result['tool_response'].append(ast.literal_eval(x[i+1].split('<tool_response>')[-1].split('</tool_response>')[0]))
            ctxs = []
            for ctx in result['tool_response'][-1]:
                for web_page in ctx['web_page_info_list']:
                    ctxs.append(
                        {
                            'search_query': ctx['search_query'],
                            "title": web_page['title'],
                            'text': web_page['quick_summary'],
                            'url': web_page['url'],
                            'id': web_page['url']
                        }
                    )
            result['ctxs'] += ctxs
        else:
            answer = x[i].split('<answer>')
            if len(answer) > 0:
                answer = answer[-1].split('</answer>')[0]
            result['output'] = answer

0 ['system\n## Background information \n* Today is 2025-05-21\n* You are Deep AI Research Assistant\n\nThe question I give you is a complex question that requires a *deep research* to answer.\n\nI will provide you with two tools to help you answer the question:\n* A web search tool to help you perform google search. \n* A webpage browsing tool to help you get new page content.\n\nYou don\'t have to answer the question now, but you should first think about the research plan or what to search next.\n\nYour output format should be one of the following two formats:\n\n<think>\nYOUR THINKING PROCESS\n</think>\n<answer>\nYOUR ANSWER AFTER GETTING ENOUGH INFORMATION\n</answer>\n\nor\n\n<think>\nYOUR THINKING PROCESS\n</think>\n<tool_call>\nYOUR TOOL CALL WITH CORRECT FORMAT\n</tool_call>\n\nYou should always follow the above two formats strictly.\nOnly output the final answer (in words, numbers or phrase) inside the <answer></answer> tag, without any explanations or extra information. If this

In [7]:
def truncate_filename(filename, max_length=125):
    """Truncate filename to max_length to ensure the filename won't exceed the file system limit.

    Args:
        filename: str
        max_length: int, default to 125 (usual path length limit is 255 chars)
    """

    if len(filename) > max_length:
        truncated_filename = filename[:max_length]
        return truncated_filename

    return filename

output_dir = '/future/u/gharshit/lotus-research/baselines/results/deepresearcher_llama4_filtered/'

for i, result in enumerate(results):
    output_file_name = output_dir + truncate_filename(str(i+1) + '_' + result['abstract']) + '.json'
    with open(output_file_name, 'w') as f:
        json.dump(result, f, indent=4)
results

[{'latency': 41.831924070138484,
  'question': 'Write a Related Works section for my academic paper. Here is my paper abstract:\nWe introduce AegisLLM, a cooperative multi-agent defense against adversarial attacks and information leakage. In AegisLLM, a structured workflow of autonomous agents — orchestrator, deflector, responder, and evaluator — collaborate to ensure safe and compliant LLM outputs, while self-improving over time through prompt optimization. We show that scaling agentic reasoning system at test-time—both by incorporating additional agent roles and by leveraging automated prompt optimization (such as DSPy)— substantially enhances robustness without compromising model utility. This test-time defense enables real-time adaptability to evolving attacks, without requiring model retraining. Comprehensive evaluations across key threat scenarios, including unlearning and jailbreaking, demonstrate the effectiveness of AegisLLM. On the WMDP unlearning benchmark, AegisLLM achieves

In [8]:
with open('/future/u/gharshit/lotus-research/baselines/results/deepresearcher_llama4_filtered/latencies.csv', 'w') as f:
    f.write('id,latency\n')
    for i, result in enumerate(results):
        f.write(f'{i+1},{result["latency"]}\n')


In [12]:
sum(latencies) / len(latencies)

42.312737009756695